In [1]:
%matplotlib inline
import matplotlib
import seaborn as sns
matplotlib.rcParams['savefig.dpi'] = 144
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource

In [2]:
import pandas as pd
import numpy as np
import math
import datetime
import matplotlib.pyplot as plt

In [3]:
myfile='loan_data.csv'
df = pd.read_csv(myfile) #, low_memory=False
rows, cols = df.shape
print rows, 'x', cols

239046 x 9


In [11]:
print df.columns

Index([u'member_id', u'loan_amnt', u'int_rate', u'issue_d', u'loan_status',
       u'fico_range_low', u'fico_range_high', u'annual_inc', u'last_pymnt_d'],
      dtype='object')


In [12]:
df.index

Int64Index([     6,      7,     10,     12,     21,     24,     27,     46,
                50,     52,
            ...
            239010, 239012, 239016, 239021, 239024, 239025, 239028, 239035,
            239038, 239040],
           dtype='int64', length=50000)

In [4]:
np.random.seed(10)
remove_n = 239046/5*4
drop_indices = np.random.choice(df.index, remove_n, replace=False)
df = df.drop(drop_indices)
print df.shape

(47810, 9)


In [5]:
df.index

Int64Index([    10,     12,     15,     19,     21,     24,     26,     46,
                47,     50,
            ...
            238989, 238992, 239000, 239011, 239014, 239016, 239021, 239023,
            239026, 239030],
           dtype='int64', length=47810)

In [26]:
rows, cols = df.shape
print rows, 'x', cols

47810 x 11


In [6]:
df.head()

member_id  loan_amnt int_rate   issue_d loan_status  fico_range_low  \
10   35944903      20000    6.03%  Oct 2014  Fully Paid             730   
12   36044643      13500    6.03%  Oct 2014     Current             715   
15   36054537       1500    9.17%  Oct 2014     Current             665   
19   36054300      10000    6.03%  Oct 2014     Current             725   
21   35944844      35000   14.49%  Oct 2014  Fully Paid             735   

    fico_range_high  annual_inc last_pymnt_d  
10              734    170000.0     Aug 2015  
12              719    105000.0     Oct 2015  
15              669     30000.0     Oct 2015  
19              729    152000.0     Oct 2015  
21              739    102765.0     May 2015

In [7]:
df['fico'] = (df.fico_range_low + df.fico_range_high)/2.0

In [19]:
df.head(20)

member_id  loan_amnt int_rate   issue_d loan_status  fico_range_low  \
10    35944903      20000    6.03%  Oct 2014  Fully Paid             730   
12    36044643      13500    6.03%  Oct 2014     Current             715   
15    36054537       1500    9.17%  Oct 2014     Current             665   
19    36054300      10000    6.03%  Oct 2014     Current             725   
21    35944844      35000   14.49%  Oct 2014  Fully Paid             735   
24    35874986      15000   10.99%  Oct 2014     Current             720   
26    35924945      10000   10.15%  Oct 2014  Fully Paid             665   
46    36024601      11675    7.69%  Oct 2014     Current             715   
47    35894893      12000   10.15%  Oct 2014     Current             715   
50    35894730       3200   16.29%  Oct 2014     Current             665   
53    35774701      19800    9.17%  Oct 2014  Fully Paid             685   
63    35844769      13600   20.99%  Oct 2014     Current             675   
66    35974759      21000   13.35%  Oct 2014     Current             680   
73    36024486       9000    6.49%  Oct 2014     Current             745   
82    35914569       3200   13.98%  Oct 2014     Current             685   
83    33840148       3000   15.61%  Oct 2014     Current             705   
88    35834655       9600   12.99%  Oct 2014     Current             695   
104   36034561      25000    8.39%  Oct 2014  Fully Paid             700   
106   35994176      26500   13.98%  Oct 2014     Current             705   
108   36014429       2500   16.29%  Oct 2014     Current             665   

     fico_range_high  annual_inc last_pymnt_d   fico  irate  
10               734    170000.0     Aug 2015  732.0   6.03  
12               719    105000.0     Oct 2015  717.0   6.03  
15               669     30000.0     Oct 2015  667.0   9.17  
19               729    152000.0     Oct 2015  727.0   6.03  
21               739    102765.0     May 2015  737.0  14.49  
24               724     63300.0     Oct 2015  722.0  10.99  
26               669     65000.0     Sep 2015  667.0  10.15  
46               719     65000.0     Oct 2015  717.0   7.69  
47               719     50000.0     Oct 2015  717.0  10.15  
50               669     60000.0     Oct 2015  667.0  16.29  
53               689    134000.0     Jun 2015  687.0   9.17  
63               679     40000.0     Oct 2015  677.0  20.99  
66               684     77000.0     Oct 2015  682.0  13.35  
73               749     64000.0     Oct 2015  747.0   6.49  
82               689     20000.0     Oct 2015  687.0  13.98  
83               709     25000.0     Oct 2015  707.0  15.61  
88               699     72000.0     Oct 2015  697.0  12.99  
104              704     85000.0     Aug 2015  702.0   8.39  
106              709    130000.0     Oct 2015  707.0  13.98  
108              669      9204.0     Oct 2015  667.0  16.29

In [10]:
output_notebook()

Loading BokehJS ...

In [11]:
from bokeh.models import (
    ColorBar,
    LinearColorMapper,
    Plot,
    Range1d,
    LinearAxis,
    FixedTicker,
    FuncTickFormatter,
)
TOOLS="pan,wheel_zoom,box_zoom,tap,box_select,lasso_select,reset,save"

In [24]:
import re
x = df['fico'].tolist()
y = [  x   for x in df['int_rate'].tolist() ]

In [12]:
df['irate'] = df['int_rate'].str.replace('%', '')
df['irate'] = pd.to_numeric(df['irate'], errors='coerce')

In [13]:
df['irate'].dtype

dtype('float64')

In [14]:
p = figure(plot_width=500, plot_height=500, tools=TOOLS,title="Avg FICO score vs Interest Rate (%)")

p.scatter(df['fico'], df['irate'], size=5, color='blue', fill_alpha=0.7, line_color=None) #fill_color='c'
p.xaxis[0].axis_label = 'FICO'
p.yaxis[0].axis_label = 'Interest Rate(%)'
show(p)

In [15]:
from scipy import stats

In [16]:
r,p = stats.pearsonr(df['fico'], df['irate'])
print r,p

-0.42296158408 0.0


# Q1. What is the relationship between FICO score and interest rate?
# A: Negative correlated, Pearson correlation coefficient R=-0.42

In [45]:
df['loan_amnt'].dtype

dtype('int64')

In [46]:
p = figure(plot_width=500, plot_height=500, tools=TOOLS,title="Loan amount vs Interest Rate (%)")

p.scatter(df['loan_amnt'], df['irate'], size=5, color='blue', fill_alpha=0.7, line_color=None) #fill_color='c'
p.xaxis[0].axis_label = 'Loan amount'
p.yaxis[0].axis_label = 'Interest Rate(%)'
show(p)

In [47]:
r2, p2 = stats.pearsonr(df['loan_amnt'], df['irate'])
print r2

-0.0947598585061


## Q2. What is the relationship between loan size and interest rate?
## A: Slightly negative correlated, Pearson correlation coefficient R= -0.095

In [29]:
dfls = df.ix[:,'loan_status']

In [30]:
dfls.head()

10    Fully Paid
12       Current
15       Current
19       Current
21    Fully Paid
Name: loan_status, dtype: object

In [ ]:
l = []
for i in range(rows):
    s = df.ix[i, 'loan_status']
    if s == 'Charged Off':
        l.append(1)
    else: 
        if s == 'Fully Paid':
            l.append(0)
        else:
            if s == 'Current':
                l.append(2)
            else: 
                print 'Error: ', s
        
    
df1= pd.DataFrame({'ilstatus': l})

In [32]:
df1 = df[df['loan_status'].astype(str) == 'Charged Off'] 

In [34]:
df2 = df[df['loan_status'].astype(str) == 'Fully Paid'] 

In [35]:
df3 = df[df['loan_status'].astype(str) == 'Current'] 

In [36]:
df1[['fico', 'irate']].describe()  #Charged off

fico       irate
count  321.000000  321.000000
mean   685.785047   15.140530
std     24.091373    3.729135
min    662.000000    6.490000
25%    667.000000   12.990000
50%    682.000000   14.990000
75%    697.000000   17.570000
max    822.000000   25.890000

In [37]:
df2[['fico', 'irate']].describe() # Fully Paid

fico        irate
count  3222.000000  3222.000000
mean    696.695996    12.261474
std      32.112822     3.748046
min     662.000000     5.320000
25%     672.000000     9.170000
50%     687.000000    12.390000
75%     712.000000    14.650000
max     847.500000    25.780000

In [38]:
df3[['fico', 'irate']].describe() # Current

fico         irate
count  44267.000000  44267.000000
mean     694.809271     11.406005
std       30.106590      3.705775
min      662.000000      5.320000
25%      672.000000      8.180000
50%      687.000000     11.530000
75%      707.000000     13.990000
max      847.500000     28.490000

## Q3. Does it seem like the size of a loan and/or the borrower's FICO score are related to whether or not the loan ends up being charged off? How might this relate to your answer to the previous question?

## A: For all 'Charged Off' events, mean FICO is 685.79 and mean Int_Rate is 15.14, compare with for all 'Fully Paid' events, mean FICO is  696.70 and mean Int_Rate is 12.26. Thus, borrowers with the lower FICO score and the higher interest rate will have higher chance ending up being charged off. This result is in agreement with previous conclusion that FICO and interest rate is negatively correlated.

In [39]:
Chargeoff = 321.0 / (3222+321)

In [40]:
Chargeoff

0.09060118543607112

## Q4. What percentage of loans have been charged off as of October 2015?
## A: 9% of loans are charged off as of Oct 2015

In [53]:
df1['lpdate'] = pd.to_datetime(df1['last_pymnt_d'])
df1['lpdate'] = df1['lpdate'].dt.strftime('%Y%m')
#pd.to_datetime(df1['last_pymnt_d'], format='%M %Y', errors='coerce')

/Users/xiangs/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':
/Users/xiangs/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


In [55]:
df1.head()

member_id  loan_amnt int_rate   issue_d  loan_status  fico_range_low  \
451    35804165       4500    7.12%  Oct 2014  Charged Off             675   
817    35993690      18000   17.57%  Oct 2014  Charged Off             695   
1178   35633223      10000   10.15%  Oct 2014  Charged Off             675   
1266   31336887       9625   15.61%  Oct 2014  Charged Off             675   
1321   33729852       5000   15.61%  Oct 2014  Charged Off             670   

      fico_range_high  annual_inc last_pymnt_d   fico  irate  lpdate  
451               679     48000.0     Jan 2015  677.0   7.12  201501  
817               699     61000.0     May 2015  697.0  17.57  201505  
1178              679     56000.0     Feb 2015  677.0  10.15  201502  
1266              679     24200.0     Jun 2015  677.0  15.61  201506  
1321              674     72012.0     Feb 2015  672.0  15.61  201502

In [58]:

df1['lpdate'] = pd.to_numeric(df1['lpdate'], errors='coerce')

/Users/xiangs/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


In [61]:
df1['lpdate'].head(20)

451     201501.0
817     201505.0
1178    201502.0
1266    201506.0
1321    201502.0
1505    201510.0
1731    201412.0
1734    201506.0
2003    201503.0
2010    201506.0
2126    201504.0
2218    201412.0
2290    201411.0
2295    201506.0
2338    201501.0
2464    201504.0
2533    201503.0
2594    201507.0
3401    201502.0
3716         NaN
Name: lpdate, dtype: float64

In [143]:
#df1['lpdate'].plot.hist(24)

## Q5. Some of the loans which are marked "Current" in October 2015 will end up being charged off before they are paid in full. Using the fact that all of these loans are 3 years in length, estimate the probability that a randomly chosen loan would eventually become charged off, possibly after October 2015. Be sure to explain any assumptions you make.


In [62]:
df.shape

(47810, 11)

In [64]:
df = df.dropna()

In [65]:
df.shape

(47570, 11)

In [66]:
df_train = df[df['loan_status'] != 'Current']

In [67]:
df_train = df_train[['loan_amnt', 'irate','issue_d', 'last_pymnt_d', 'annual_inc', 'loan_status' ]]

In [104]:
df_train['lpdate'] = pd.to_datetime(df_train['last_pymnt_d'])
df_train['lpdate'] = df_train['lpdate'].dt.strftime('%Y%m')
df_train['lpdate'] = pd.to_numeric(df_train['lpdate'], errors='coerce',downcast='integer')

In [106]:
df_train['idate'] = pd.to_datetime(df_train['issue_d'])
df_train['idate'] = df_train['idate'].dt.strftime('%Y%m')
df_train['idate'] = pd.to_numeric(df_train['idate'], errors='coerce',downcast='integer')

In [107]:
df_train.head()

loan_amnt  irate   issue_d last_pymnt_d  annual_inc loan_status  lpdate  \
10       20000   6.03  Oct 2014     Aug 2015    170000.0  Fully Paid  201508   
21       35000  14.49  Oct 2014     May 2015    102765.0  Fully Paid  201505   
26       10000  10.15  Oct 2014     Sep 2015     65000.0  Fully Paid  201509   
53       19800   9.17  Oct 2014     Jun 2015    134000.0  Fully Paid  201506   
104      25000   8.39  Oct 2014     Aug 2015     85000.0  Fully Paid  201508   

      idate  status  
10   201410       0  
21   201410       0  
26   201410       0  
53   201410       0  
104  201410       0

In [108]:
df_train.ix[10,'loan_status']

'Fully Paid'

In [85]:
#df_train.assign(status = lambda df_train: 1 if df_train['loan_status'] == 'Fully Paid' else 0)
f = lambda x: 0 if x == 'Fully Paid' else 1
df_train['status'] = df_train['loan_status'].apply(f)


In [109]:
df_train.head()
X_train = df_train[['loan_amnt','irate','idate', 'lpdate', 'annual_inc']]
y_train = df_train[['status']]

In [110]:
X = X_train.values
y = y_train.values

In [111]:
print type(X)
print type(y)
print X.shape
print y.shape

<type 'numpy.ndarray'>
<type 'numpy.ndarray'>
(3531, 5)
(3531, 1)


In [112]:
X[:2]

array([[  2.00000000e+04,   6.03000000e+00,   2.01410000e+05,
          2.01508000e+05,   1.70000000e+05],
       [  3.50000000e+04,   1.44900000e+01,   2.01410000e+05,
          2.01505000e+05,   1.02765000e+05]])

In [123]:
from sklearn.linear_model import LogisticRegression
C = 10.0
classifiers = {'L1 logistic': LogisticRegression(C=C, penalty='l1'),
               'L2 logistic (OvR)': LogisticRegression(C=C, penalty='l2')}


classifier = LogisticRegression(C=C, penalty='l1')



In [124]:
classifier.fit(X, y)

LogisticRegression(C=10.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l1', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [125]:
y_pred = classifier.predict(X)

In [126]:
dif = y - y_pred

In [ ]:
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline
from sklearn.linear_model import Ridge
from sklearn import datasets, linear_model, utils, preprocessing
from sklearn.base import BaseEstimator, RegressorMixin, TransformerMixin
from sklearn import neighbors
from sklearn import ensemble
from sklearn.pipeline import Pipeline, FeatureUnion

class EnsembleTransformer(BaseEstimator, TransformerMixin):
    
    def __init__(self, base_estimator, residual_estimators):
        self.base_estimator = base_estimator
        self.residual_estimators = residual_estimators
    
    def fit(self, X, y):
        self.base_estimator.fit(X, y)
        y_err = y - self.base_estimator.predict(X)
        for est in self.residual_estimators:
            est.fit(X, y_err)
        return self
    
    def transform(self, X):
        all_ests = [self.base_estimator] + list(self.residual_estimators)
        return np.array([est.predict(X) for est in all_ests]).T


ensemble_pipe = Pipeline([
        ('logi', LogisticRegression(C=C,penalty='l1') ),
        ('ensemble', EnsembleTransformer(
                LogisticRegression(C=C,penalty='l1'),
                (neighbors.KNeighborsRegressor(n_neighbors=10),
                 ensemble.RandomForestRegressor(min_samples_leaf=10)))),
        ('blend', LogisticRegression(C=C, penalty='l2'))
    ])


#rang = range(1,5)
#param_grid = dict(C = rang)
#grid_search = GridSearchCV(classifier, param_grid=param_grid, verbose=10)
#grid_search.fit(X,y)  #X, y
#print(grid_search.best_estimator_)

ensemble_pipe.fit(X,y)

In [132]:
df_test = df[df['loan_status'] == 'Current']
df_test = df_test[['loan_amnt', 'irate','issue_d', 'last_pymnt_d', 'annual_inc', 'loan_status' ]]

In [133]:
df_test['lpdate'] = pd.to_datetime(df_test['last_pymnt_d'])
df_test['lpdate'] = df_test['lpdate'].dt.strftime('%Y%m')
df_test['lpdate'] = pd.to_numeric(df_test['lpdate'], errors='coerce',downcast='integer')
df_test['idate'] = pd.to_datetime(df_test['issue_d'])
df_test['idate'] = df_test['idate'].dt.strftime('%Y%m')
df_test['idate'] = pd.to_numeric(df_test['idate'], errors='coerce',downcast='integer')

In [137]:
df_test = df_test[['loan_amnt','irate','idate', 'lpdate', 'annual_inc']]
X_test = df_test.values

In [138]:
X_test[:2]

array([[  1.35000000e+04,   6.03000000e+00,   2.01410000e+05,
          2.01510000e+05,   1.05000000e+05],
       [  1.50000000e+03,   9.17000000e+00,   2.01410000e+05,
          2.01510000e+05,   3.00000000e+04]])

In [139]:

probas = classifier.predict_proba(X_test)

In [141]:
probas[:20]

array([[ 0.97812494,  0.02187506],
       [ 0.95917313,  0.04082687],
       [ 0.98088816,  0.01911184],
       [ 0.94191036,  0.05808964],
       [ 0.96834709,  0.03165291],
       [ 0.94951607,  0.05048393],
       [ 0.87113714,  0.12886286],
       [ 0.71467949,  0.28532051],
       [ 0.91176247,  0.08823753],
       [ 0.97492231,  0.02507769],
       [ 0.90386458,  0.09613542],
       [ 0.87615046,  0.12384954],
       [ 0.92320514,  0.07679486],
       [ 0.90848557,  0.09151443],
       [ 0.8581789 ,  0.1418211 ],
       [ 0.97418845,  0.02581155],
       [ 0.9706768 ,  0.0293232 ],
       [ 0.96456454,  0.03543546],
       [ 0.78379057,  0.21620943],
       [ 0.96896098,  0.03103902]])

In [142]:
classifier.classes_

array([0, 1])

## A5: I used logistic regression (scikit-learn) to learn 'Fully Paid'=0 vs 'Charged Off'=1 categories with the input features 'loan_amnt', 'irate','issue_d', 'last_pymnt_d', 'annual_inc', 'loan_status', then the probability of such 'Current' loans can be calculated via the same input, and array `probas` contains all the probability of ending in 'Fully Paid'=0, and 'Charged Off'=1. Such as the first example, Prob(Fully Paid)=0.978, Prob(Charged off)=0.022.